In [1]:
import os
if "ntbk" in os.getcwd():
    os.chdir("..")
print(os.getcwd())

import sys
sys.path.append(os.path.join(os.getcwd(), "otgnn"))


%load_ext autoreload
%autoreload 2

from otgnn.models import GCN
from otgnn.graph import MolGraph
from otgnn.utils import save_model, load_model

from mol_opt.mol_opt import MolOpt
from mol_opt.data_mol_opt import MolOptDataset
from mol_opt.data_mol_opt import get_loader
from mol_opt.arguments import get_args
from mol_opt.train_mol_opt import main, get_latest_model
from mol_opt.ot_utils import compute_barycenter

from rdkit.Chem import MolFromSmiles

import torch
import numpy as np
import time
import torch.nn.functional as F

/home/octav/gitrepos/tum-thesis


In [2]:
model_type = "deepsets"
sys.argv = ["", "-cuda", "-model_type", model_type]
args = get_args()
outdir_suffix = "dev4"
args.n_epochs = 20000 
args.init_model = "{}-attention-sink3-test1".format(model_type)
# args.init_model = "{}-test1".format(model_type)
args.init_decoder_model = "{}_decode".format(args.init_model)
args.output_dir = "mol_opt/output_{}/{}".format(outdir_suffix, args.init_model)
args.tb_logs_dir = "mol_opt/logs_{}/{}".format(outdir_suffix, args.init_model)
args.batch_size = 50 

args.penalty_gumbel = False 

args.scale_lambdas = True
args.connectivity = True 
args.valency = True 
args.euler_characteristic_penalty = True
args.conn_lambda_start = 0.001
args.conn_lambda_end = 3
args.conn_lambda_epochs_start = 4001
args.conn_lambda_epochs_end = 12000
args.valency_lambda_start = 0.001
args.valency_lambda_end = 5
args.valency_lambda_epochs_start = 4001
args.valency_lambda_epochs_end = 12000
args.euler_lambda_start = 0.001 
args.euler_lambda_end = 2 
args.euler_lambda_epochs_start = 4001
args.euler_lambda_epochs_end = 12000
args.tau_start = 1
args.tau_end = 0.01
args.tau_epochs_start = 1
args.tau_epochs_end = 12000

args.cross_att_use = True
args.cross_att_random = False
args.cross_att_n_sinkhorn = 3
# args.morgan_bits = 1024

args.conn_penalty_function = "capped_logdet" 

print(args, '\n')

Namespace(N_transformer=6, agg_func='sum', batch_norm=False, batch_size=50, conn_lambda_end=3, conn_lambda_epochs_end=12000, conn_lambda_epochs_start=4001, conn_lambda_start=0.001, conn_penalty_function='capped_logdet', connectivity=True, connectivity_hard=False, cross_att_dim=150, cross_att_n_sinkhorn=3, cross_att_random=False, cross_att_use=True, cuda=True, device='cuda:0', dim_tangent_space=40, dropout_ffn=0.0, dropout_gcn=0.0, dropout_transformer=0.1, euler_characteristic_penalty=True, euler_lambda_end=2, euler_lambda_epochs_end=12000, euler_lambda_epochs_start=4001, euler_lambda_start=0.001, ffn_activation='LeakyReLU', init_decoder_model='deepsets-attention-sink3-test1_decode', init_model='deepsets-attention-sink3-test1', linear_out=False, max_num_atoms=70, model_type='deepsets', morgan_bits=0, n_epochs=20000, n_ffn_hidden=100, n_ffn_transformer=100, n_heads_transformer=10, n_hidden=200, n_labels=1, n_layers=5, one_batch_train=False, ot_solver='emd', output_dir='mol_opt/output_dev

In [3]:
# train_data_loader = get_loader("iclr19-graph2graph/data/qed", "train_pairs", args.batch_size, same_number_atoms = True)
# train_data_loader = get_loader("molgen/data/chembl50", "train", args.batch_size, same_number_atoms = True)
# val_data_loader = get_loader("iclr19-graph2graph/data/qed", "valid", 36, False)

train_data_loader = get_loader("molgen/data/chembl50", "train", args.batch_size, same_number_atoms = True)
# val_data_loader = get_loader("molgen/data/chembl50", "val_split", args.batch_size, same_number_atoms = True)
val_data_loader = None

In [4]:
molopt, molopt_decoder = main(args, train_data_loader = train_data_loader, val_data_loader = val_data_loader)

No model deepsets-attention-sink3-test1 found in mol_opt/output_dev4/deepsets-attention-sink3-test1! Starting from scratch.
Penalty params: tau=1.00000 conn_l=0.00100 val_l=0.00100 euler_l=0.00100 epoch=-1 mode=[0 0 0] conn=True val=True euler=True
Epoch: 1


/home/octav/gitrepos/tum-thesis/otgnn/models/gromov_modules.py:398: UserWarning: Implicit dimension choice for log_softmax has been deprecated. Change the call to include dim=X as an argument.
  nce_reg = torch.nn.LogSoftmax()(torch.stack(all_nce_dists))[0]


Losses Batch 0, train
 fgw:5207.0721875
 conn_penalty:0.0000000
 val_penalty:709.6667969
 euler_penalty:197.1428711
 total:5207.9781250
Penalty params: tau=1.00000 conn_l=0.00100 val_l=0.00100 euler_l=0.00100 epoch=1 mode=[0 0 0] conn=False val=False euler=False
Penalty params: tau=1.00000 conn_l=0.00100 val_l=0.00100 euler_l=0.00100 epoch=1 mode=[0 0 0] conn=False val=False euler=False
Losses Epoch 1, train
 fgw:5207.0721875
 conn_penalty:0.0000000
 val_penalty:709.6667969
 euler_penalty:197.1428711
 total:5207.9781250
Epoch duration: 4.1085569858551025
Saving model, do not interrupt...
Saved at mol_opt/output_dev4/deepsets-attention-sink3-test1/model_deepsets-attention-sink3-test1_1
Epoch: 2
Losses Batch 0, train
 fgw:3309.1662500
 conn_penalty:0.0000000
 val_penalty:0.0000000
 euler_penalty:0.0000000
 total:3309.1662500
Penalty params: tau=0.99962 conn_l=0.00100 val_l=0.00100 euler_l=0.00100 epoch=2 mode=[0 0 0] conn=False val=False euler=False
Penalty params: tau=0.99962 conn_l=0.0

Losses Batch 0, train
 fgw:422.5833984
 conn_penalty:0.0000000
 val_penalty:0.0000000
 euler_penalty:0.0000000
 total:422.5833984
Penalty params: tau=0.99541 conn_l=0.00100 val_l=0.00100 euler_l=0.00100 epoch=13 mode=[0 0 0] conn=False val=False euler=False
Penalty params: tau=0.99541 conn_l=0.00100 val_l=0.00100 euler_l=0.00100 epoch=13 mode=[0 0 0] conn=False val=False euler=False
Losses Epoch 13, train
 fgw:422.5833984
 conn_penalty:0.0000000
 val_penalty:0.0000000
 euler_penalty:0.0000000
 total:422.5833984
Epoch duration: 0.7620267868041992
Saving model, do not interrupt...
Saved at mol_opt/output_dev4/deepsets-attention-sink3-test1/model_deepsets-attention-sink3-test1_13
Epoch: 14
Losses Batch 0, train
 fgw:401.3099609
 conn_penalty:0.0000000
 val_penalty:0.0000000
 euler_penalty:0.0000000
 total:401.3099609
Penalty params: tau=0.99502 conn_l=0.00100 val_l=0.00100 euler_l=0.00100 epoch=14 mode=[0 0 0] conn=False val=False euler=False
Penalty params: tau=0.99502 conn_l=0.00100 val

Losses Batch 0, train
 fgw:305.1999023
 conn_penalty:0.0000000
 val_penalty:0.0000000
 euler_penalty:0.0000000
 total:305.1999023
Penalty params: tau=0.99083 conn_l=0.00100 val_l=0.00100 euler_l=0.00100 epoch=25 mode=[0 0 0] conn=False val=False euler=False
Penalty params: tau=0.99083 conn_l=0.00100 val_l=0.00100 euler_l=0.00100 epoch=25 mode=[0 0 0] conn=False val=False euler=False
Losses Epoch 25, train
 fgw:305.1999023
 conn_penalty:0.0000000
 val_penalty:0.0000000
 euler_penalty:0.0000000
 total:305.1999023
Epoch duration: 0.8347883224487305
Saving model, do not interrupt...
Saved at mol_opt/output_dev4/deepsets-attention-sink3-test1/model_deepsets-attention-sink3-test1_25
Epoch: 26
Losses Batch 0, train
 fgw:302.9769336
 conn_penalty:0.0000000
 val_penalty:0.0000000
 euler_penalty:0.0000000
 total:302.9769336
Penalty params: tau=0.99045 conn_l=0.00100 val_l=0.00100 euler_l=0.00100 epoch=26 mode=[0 0 0] conn=False val=False euler=False
Penalty params: tau=0.99045 conn_l=0.00100 val

...

Losses Batch 0, train
 fgw:222.0919531
 conn_penalty:173.6709961
 val_penalty:22.9947461
 euler_penalty:21.9980249
 total:227.3868750
Penalty params: tau=0.06366 conn_l=0.02403 val_l=0.02943 euler_l=0.02046 epoch=7177 mode=[1 1 1] conn=True val=True euler=True
Penalty params: tau=0.06366 conn_l=0.02403 val_l=0.02943 euler_l=0.02046 epoch=7177 mode=[1 1 1] conn=True val=True euler=True
Losses Epoch 7177, train
 fgw:222.0919531
 conn_penalty:173.6709961
 val_penalty:22.9947461
 euler_penalty:21.9980249
 total:227.3868750
Epoch duration: 4.616758108139038
Saving model, do not interrupt...
Saved at mol_opt/output_dev4/deepsets-attention-sink3-test1/model_deepsets-attention-sink3-test1_7177
Epoch: 7178
Losses Batch 0, train
 fgw:222.0819922
 conn_penalty:173.9445117
 val_penalty:22.9972461
 euler_penalty:21.9986621
 total:227.3888867
Penalty params: tau=0.06364 conn_l=0.02405 val_l=0.02947 euler_l=0.02048 epoch=7178 mode=[1 1 1] conn=True val=True euler=True
Penalty params: tau=0.06364 conn

Losses Batch 0, train
 fgw:222.0878320
 conn_penalty:174.0550195
 val_penalty:22.9980249
 euler_penalty:21.9990308
 total:227.4564648
Penalty params: tau=0.06337 conn_l=0.02432 val_l=0.02981 euler_l=0.02069 epoch=7189 mode=[1 1 1] conn=True val=True euler=True
Penalty params: tau=0.06337 conn_l=0.02432 val_l=0.02981 euler_l=0.02069 epoch=7189 mode=[1 1 1] conn=True val=True euler=True
Losses Epoch 7189, train
 fgw:222.0878320
 conn_penalty:174.0550195
 val_penalty:22.9980249
 euler_penalty:21.9990308
 total:227.4564648
Epoch duration: 4.698649883270264
Saving model, do not interrupt...
Saved at mol_opt/output_dev4/deepsets-attention-sink3-test1/model_deepsets-attention-sink3-test1_7189
Epoch: 7190
Losses Batch 0, train
 fgw:222.1052148
 conn_penalty:173.6774023
 val_penalty:22.9943018
 euler_penalty:21.9979980
 total:227.4699023
Penalty params: tau=0.06335 conn_l=0.02435 val_l=0.02984 euler_l=0.02071 epoch=7190 mode=[1 1 1] conn=True val=True euler=True
Penalty params: tau=0.06335 conn

Losses Batch 0, train
 fgw:222.0531445
 conn_penalty:173.8006055
 val_penalty:22.9969116
 euler_penalty:21.9986060
 total:227.4805859
Penalty params: tau=0.06308 conn_l=0.02461 val_l=0.03020 euler_l=0.02093 epoch=7201 mode=[1 1 1] conn=True val=True euler=True
Penalty params: tau=0.06308 conn_l=0.02461 val_l=0.03020 euler_l=0.02093 epoch=7201 mode=[1 1 1] conn=True val=True euler=True
Losses Epoch 7201, train
 fgw:222.0531445
 conn_penalty:173.8006055
 val_penalty:22.9969116
 euler_penalty:21.9986060
 total:227.4805859
Epoch duration: 4.546077251434326
Saving model, do not interrupt...
Saved at mol_opt/output_dev4/deepsets-attention-sink3-test1/model_deepsets-attention-sink3-test1_7201
Epoch: 7202
Losses Batch 0, train
 fgw:222.0575586
 conn_penalty:173.7174023
 val_penalty:22.9963037
 euler_penalty:21.9984448
 total:227.4883789
Penalty params: tau=0.06306 conn_l=0.02464 val_l=0.03023 euler_l=0.02095 epoch=7202 mode=[1 1 1] conn=True val=True euler=True
Penalty params: tau=0.06306 conn

Losses Batch 0, train
 fgw:222.0489648
 conn_penalty:173.6288867
 val_penalty:22.9948315
 euler_penalty:21.9979468
 total:227.5378906
Penalty params: tau=0.06279 conn_l=0.02491 val_l=0.03058 euler_l=0.02117 epoch=7213 mode=[1 1 1] conn=True val=True euler=True
Penalty params: tau=0.06279 conn_l=0.02491 val_l=0.03058 euler_l=0.02117 epoch=7213 mode=[1 1 1] conn=True val=True euler=True
Losses Epoch 7213, train
 fgw:222.0489648
 conn_penalty:173.6288867
 val_penalty:22.9948315
 euler_penalty:21.9979468
 total:227.5378906
Epoch duration: 4.540026903152466
Saving model, do not interrupt...
Saved at mol_opt/output_dev4/deepsets-attention-sink3-test1/model_deepsets-attention-sink3-test1_7213
Epoch: 7214


KeyboardInterrupt: 